In [ ]:
20

In [ ]:
20

In [1]:
from federatedscope.register import register_data
from federatedscope.register import register_trainer
from federatedscope.register import register_metric
from federatedscope.register import register_model




### Register model

In [2]:
#from federatedscope.contrib.model.mnist_model import call_my_net
#register_model("mynet", call_my_net)

### Register trainer

In [3]:

from federatedscope.contrib.trainer.laplacian_trainer_with_domain_separation_VAE_separated_other_diff_other_sim import call_laplacian_trainer

register_trainer('laplacian_trainer', call_laplacian_trainer)

/home/michael/Master-Thesis/CKIM_Competition/venv/lib/python3.9/site-packages/torch_geometric/graphgym/imports.py:14: UserWarning: Please install 'pytorch_lightning' for using the GraphGym experiment manager via 'pip install pytorch_lightning'
  warnings.warn("Please install 'pytorch_lightning' for using the GraphGym "
/home/michael/Master-Thesis/CKIM_Competition/venv/lib/python3.9/site-packages/torch_geometric/graphgym/logger.py:23: UserWarning: Please install 'pytorch_lightning' for using the GraphGym experiment manager via 'pip install pytorch_lightning'
  warnings.warn("Please install 'pytorch_lightning' for using the GraphGym "


Device: cuda


### Register metric

### Create the config

#### Set data, model, trainer and metric

In [4]:
from federatedscope.core.configs.config import global_cfg, CN
cfg = global_cfg.clone()

cfg.merge_from_file("scripts/B-FHTL_exp_scripts/Graph-DT/fed_dom_sep_otherDiff_otherSim.yaml")
cfg.data.save_dir = 'test_dir'
# cfg.data.type = 'cikm_cup'
#cfg.data.root = 'data'
#cfg.data.shuffle=True
#cfg.data.transform = [['ToTensor'], ['Normalize', {'mean': [0.], 'std': [1]}]]
#cfg.model.type = 'gin'
#cfg.model.out_channels = 10
#cfg.model.hidden = 64
#cfg.model.task='graph'
#cfg.model.dropout = 0.5
#cfg.personalization.local_param = ['encoder_atom', 'encoder', 'clf']#['node_encoder', 'clf']
#cfg.train.batch_or_epoch = "epoch"
cfg.trainer.type = 'laplacian_trainer'
cfg.data.batch_size = 64
# cfg.eval.metric = ['mymetric']
cfg.params = CN()
cfg.params.alpha=0.1
cfg.params.csd_importance= 1e2
cfg.params.sim_importance = 0.
cfg.params.diff_importance = 0.
cfg.params.eps=1e-20
cfg.params.p=0.
cfg.params.lam = 0.
cfg.params.recon_importance = 0.
cfg.params.kld_importance = 0.
cfg.model.dropout=0.


#### configure other options

In [5]:
#cfg.use_gpu = True 0.05 [0.02-0.03] 0.04-0.06
#cfg.best_res_update_round_wise_key = "test_loss"

#cfg.federate.mode = 'standalone'

cfg.federate.method = \
    f'Laplacian_MINE_VAE_test_no_KLD'

#cfg.federate.local_update_steps = 20000000
cfg.personalization.local_update_steps = 20000000
#cfg.finetune.local_update_steps = 20000000
#cfg.train.local_update_steps = 1

cfg.federate.total_round_num = 2000
cfg.federate.client_num = 2
cfg.early_stop.patience = 3000
#cfg.train.optimizer.lr = 0.001
#cfg.train.optimizer.weight_decay = 0.0005
#cfg.grad.grad_clip = 2.0
cfg.criterion.type = 'CrossEntropyLoss'
#cfg.seed = 123
cfg.eval.freq = 1
cfg.eval.metrics = ['imp_ratio']
cfg.eval.report = ['avg']
cfg.eval.best_res_update_round_wise_key = 'val_imp_ratio'


In [6]:
import torch
#torch.manual_seed(0)
#torch.backends.cudnn.benchmark = False
#torch.use_deterministic_algorithms(F/home/michael/Desktop/backup files/FederatedScope/data/CIKM22Competitionalse)
#import random
#random.seed(0)
#import numpy as np
#np.random.seed(0)

In [7]:
from yacs.config import CfgNode
client_cfg_file = "scripts/B-FHTL_exp_scripts/Graph-DT/cfg_per_client_theirs.yaml"# "scripts/B-FHTL_exp_scripts/Graph-DT/cfg_per_client_ours_lr_local_steps.yaml"
client_cfg = CfgNode.load_cfg(open(client_cfg_file,
                                       'r')) if client_cfg_file else None


### Start the FL prosess

In [8]:
from federatedscope.core.auxiliaries.data_builder import get_data
from federatedscope.core.auxiliaries.utils import setup_seed, update_logger
from federatedscope.core.fed_runner import FedRunner
from federatedscope.core.auxiliaries.worker_builder import get_server_cls, get_client_cls


2023-01-14 16:33:42,717 (trainer_builder:11)WARNING: No module named 'federatedscope.contrib.optimizer' in `federatedscope.contrib.trainer`, some modules are not available.


In [9]:
from federatedscope.contrib.workers.laplacian_with_domain_separation_MI_client import LaplacianDomainSeparationMIClient
from federatedscope.contrib.workers.laplacian_server_dom_sep import LaplacianServerDomSep

setup_seed(cfg.seed)
update_logger(cfg)
data, modified_cfg = get_data(cfg)
cfg.merge_from_other_cfg(modified_cfg)


2023-01-14 16:33:42,726 (utils:129)INFO: the current machine is at 127.0.1.1
2023-01-14 16:33:42,727 (utils:131)INFO: the current dir is /home/michael/Master-Thesis/CKIM_Competition
2023-01-14 16:33:42,727 (utils:132)INFO: the output dir is exp/test_dir/Laplacian_MINE_VAE_test_no_KLD_gin_on_graph-dt_lr0.1_lstep1_/sub_exp_20230114163342


In [10]:
from federatedscope.contrib.workers.laplacian_with_domain_separation_VAE_Separated_otherDiff_otherSim_client import LaplacianDomainSeparation1MINE_Separated_OtherDiff_OtherSim_Client
from federatedscope.contrib.workers.laplacian_with_domain_separation_1MINE_Other_DiffLoss_VAE_client import LaplacianDomainSeparation1MINEOtherDiffClient
from federatedscope.contrib.workers.laplacian_server import LaplacianServer

Fed_runner = FedRunner(data=data,
                       server_class=LaplacianServer,
                       client_class=LaplacianDomainSeparation1MINE_Separated_OtherDiff_OtherSim_Client,
                       config=cfg.clone(),
                       client_config=client_cfg)
Fed_runner.run()

diff_local_global: 0.06492108851671219
mi_global_fixed: -5.587935447692871e-09
rec_loss: 0.45180556178092957
kld_loss: 1.3099277019500732
diff_local_global: 0.08453540503978729
mi_global_fixed: 0.0031833909451961517
rec_loss: 0.46664974093437195
kld_loss: 1.280057430267334
diff_local_global: 0.08001713454723358
mi_global_fixed: 0.007658866234123707
rec_loss: 0.4689767062664032
kld_loss: 1.2884376049041748
diff_local_global: 0.07372604310512543
mi_global_fixed: 0.004733646288514137
rec_loss: 0.43615883588790894
kld_loss: 1.3182947635650635
diff_local_global: 0.0696057602763176
mi_global_fixed: 0.004896111786365509
rec_loss: 0.45472434163093567
kld_loss: 1.2696009874343872
diff_local_global: 0.0715903788805008
mi_global_fixed: 0.004975081421434879
rec_loss: 0.466806560754776
kld_loss: 1.2845584154129028
diff_local_global: 0.07456246018409729
mi_global_fixed: 0.010847451165318489
rec_loss: 0.444694846868515
kld_loss: 1.303312063217163
rho: 0.0
server params: 
encoder_atom.atom_embedding_l

/home/michael/Master-Thesis/CKIM_Competition/venv/lib/python3.9/site-packages/torch/nn/init.py:405: UserWarning: Initializing zero-element tensors is a no-op
  warnings.warn("Initializing zero-element tensors is a no-op")


diff_local_global: 0.07303828746080399
mi_global_fixed: 0.01377137377858162
rec_loss: 0.45470955967903137
kld_loss: 1.2862722873687744
diff_local_global: 0.07125454396009445
mi_global_fixed: 0.008539116010069847
rec_loss: 0.449950248003006
kld_loss: 1.2755963802337646


2023-01-14 16:33:45,837 (fed_runner:249)INFO: Server #0 has been set up ... 
2023-01-14 16:33:45,854 (config:261)INFO: the used configs are: 
asyn:
  min_received_num: 2
  min_received_rate: -1.0
  timeout: 0
  use: True
attack:
  alpha_TV: 0.001
  alpha_prop_loss: 0
  attack_method: 
  attacker_id: -1
  classifier_PIA: randomforest
  info_diff_type: l2
  inject_round: 0
  max_ite: 400
  reconstruct_lr: 0.01
  reconstruct_optim: Adam
  target_label_ind: -1
backend: torch
cfg_file: 
criterion:
  type: MSELoss
data:
  args: []
  batch_size: 64
  cSBM_phi: [0.5, 0.5, 0.5]
  consistent_label_distribution: False
  drop_last: False
  graphsaint:
    num_steps: 30
    walk_length: 2
  loader: 
  num_workers: 0
  pre_transform: []
  quadratic:
    dim: 1
    max_curv: 12.5
    min_curv: 0.02
  root: data/
  save_dir: test_dir
  server_holds_all: False
  shuffle: True
  sizes: [10, 5]
  splits: [0.8, 0.1, 0.1]
  splitter: ooxx
  splitter_args: []
  subsample: 1.0
  target_transform: []
  transf

diff_local_global: 0.07227684557437897
mi_global_fixed: 0.008258190006017685
rec_loss: 0.4636536240577698
kld_loss: 1.2810276746749878
encoder_atom.atom_embedding_list.1.weight
encoder_atom.atom_embedding_list.2.weight
encoder_atom.atom_embedding_list.3.weight
encoder_atom.atom_embedding_list.4.weight
encoder_atom.atom_embedding_list.5.weight
encoder_atom.atom_embedding_list.6.weight
encoder_atom.atom_embedding_list.7.weight
encoder_atom.atom_embedding_list.8.weight
encoder_atom.atom_embedding_list.9.weight
encoder_atom.atom_embedding_list.10.weight
encoder_atom.atom_embedding_list.11.weight
encoder_atom.atom_embedding_list.12.weight
encoder_atom.atom_embedding_list.13.weight
encoder_atom.atom_embedding_list.14.weight
encoder_atom.atom_embedding_list.15.weight
encoder_atom.atom_embedding_list.16.weight
encoder_atom.atom_embedding_list.17.weight
encoder_atom.atom_embedding_list.18.weight
encoder_atom.atom_embedding_list.19.weight
encoder_atom.atom_embedding_list.20.weight
encoder_atom.a

...

in val or test
diff_local_global: 0.04910777136683464
mi_global_fixed: 0.0028459178283810616
rec_loss: 0.1425890028476715
kld_loss: 0.7784600257873535
diff_local_global: 0.03333289921283722
mi_global_fixed: 0.0035325202625244856
rec_loss: 0.12229244410991669
kld_loss: 0.8023414611816406
in val or test
diff_local_global: 0.052114445716142654
mi_global_fixed: 0.0030484460294246674
rec_loss: 0.1253691017627716
kld_loss: 0.8018783330917358
diff_local_global: 0.030451780185103416
mi_global_fixed: 0.00417765649035573
rec_loss: 0.1310686618089676
kld_loss: 0.7941450476646423


2023-01-14 18:51:55,095 (client:410)INFO: {'Role': 'Client #1', 'Round': 1057, 'Results_raw': {'test_imp_ratio': -4.280077, 'test_avg_loss': 0.963861, 'test_total': 113, 'test_loss': 108.916252, 'val_imp_ratio': 23.73528, 'val_avg_loss': 0.704915, 'val_total': 113, 'val_loss': 79.655371}}
2023-01-14 18:51:55,096 (monitor:513)INFO: current_best=39.252943, should_save=False


in val or test
diff_local_global: 0.04246893525123596
mi_global_fixed: 0.001508559100329876
rec_loss: 0.009524829685688019
kld_loss: 0.12739300727844238
in val or test
diff_local_global: 0.027215730398893356
mi_global_fixed: 0.001533044851385057
rec_loss: 0.018487626686692238
kld_loss: 0.11078102141618729


2023-01-14 18:51:55,479 (client:410)INFO: {'Role': 'Client #2', 'Round': 1057, 'Results_raw': {'test_imp_ratio': 24.977489, 'test_avg_loss': 0.019881, 'test_total': 64, 'test_loss': 1.272382, 'val_imp_ratio': 12.444024, 'val_avg_loss': 0.023202, 'val_total': 63, 'val_loss': 1.461747}}
2023-01-14 18:51:55,480 (monitor:513)INFO: current_best=49.151425, should_save=False


diff_local_global: 0.05170813947916031
mi_global_fixed: -2.7939677238464355e-09
rec_loss: 0.13162566721439362
kld_loss: 0.7694957256317139
diff_local_global: 0.05549437552690506
mi_global_fixed: 0.0028402451425790787
rec_loss: 0.11982597410678864
kld_loss: 0.7845520973205566
diff_local_global: 0.053909581154584885
mi_global_fixed: 0.003164357505738735
rec_loss: 0.11557376384735107
kld_loss: 0.7941069602966309
diff_local_global: 0.05236314982175827
mi_global_fixed: 0.003105386160314083
rec_loss: 0.13014182448387146
kld_loss: 0.7745112776756287
diff_local_global: 0.04354962706565857
mi_global_fixed: 0.00314138550311327
rec_loss: 0.1311061531305313
kld_loss: 0.7979389429092407
diff_local_global: 0.04896663501858711
mi_global_fixed: 0.002700437791645527
rec_loss: 0.12362165004014969
kld_loss: 0.7923985123634338
diff_local_global: 0.05501645803451538
mi_global_fixed: 0.004815761931240559
rec_loss: 0.12441293895244598
kld_loss: 0.7906628847122192
diff_local_global: 0.04858282953500748
mi_glo

client 0 times: 0.346s
bei normal fedavg: 0.15s
mit MINE: 1.7 Sekunden


+

In [ ]:
777-431


In [ ]:
data

In [ ]:
import os

,,0After 10 rounds:

diff: 0, csd: 0:
server: -8
c1 t/val: 0.375 /0.37
c2 t/val: 0.678 /0.606
c3 t/val: 0.699 /0.608
c4 t/val: 0.599 /0.537

diff: 0, csd: 0:
server: -4.5
c1 t/val: 0.372879 /0.328
c2 t/val: 0.678992 /0.605809
c3 t/val: 0.70166 /0.608609
c4 t/val: 0.597455 /0.534253



diff: 10, csd: 0:
server: -35
c1 t/val: 0.482/0.52
c2 t/val: 0.694/0.65
c3 t/val: 0.724/0.65
c4 t/val: 0.674/0.575

diff: 1, csd: 0:
server: -9.6
c1 t/val: 0.378194/0.319349
c2 t/val: 0.67461/0.609163
c3 t/val: 0.705559/0.615019
c4 t/val: 0.605581/0.572086

diff: 0, csd: 1e4:
server: -18
c1 t/val: 0.280962/0.23074
c2 t/val: 0.682652/0.603175
c3 t/val: 0.699094/0.67027
c4 t/val: 0.594985/0.609611

diff: 0 csd: 1e8
server: -18
c1 t/val: 0.2606/0.348(0.197)
c2 t/val: 0.653/0.0.602
c3 t/val: 0.691/0.597
c4 t/val: 0.581/0.629

diff: 0 csd: 1e8
server: -12.7
c1 t/val: 0.262647/0.249875
c2 t/val: 0.649273/0.0.600435
c3 t/val: 0.696132/0.615158
c4 t/val: 0.586597/0.656992


diff: 0.1 csd: 0
server: -11
c1 t/val: 0.2606/0.332837
c2 t/val: 0.678326/0.0.610099
c3 t/val: 0.704083/0.616179
c4 t/val: 0.604177/0.559658




In [ ]:
os.environ['CUBLAS_WORKSPACE_CONFIG']